# Goal

Show all London subway stations

## Imports and generic utility methods

In [17]:
import duckdb
import geopandas as gpd
import pandas as pd
from shapely import wkt

In [2]:
def duckdb_connection():
    conn = duckdb.connect()
    conn.install_extension('spatial')
    conn.load_extension('spatial')
    return conn

In [11]:
def load_area(conn, overture_local_base, overture_theme, overture_type, bbox):
    (minx,miny,maxx,maxy) = bbox
    path = f"{overture_local_base}/theme={overture_theme}/type={overture_type}/*"
    query = f"""
    SELECT * EXCLUDE(geometry), ST_AsText(geometry) AS geometry 
    FROM read_parquet('{path}')
    WHERE bbox.xmin >= {minx}
      AND bbox.xmax <= {maxx}
      AND bbox.ymin >= {miny}
      AND bbox.ymax <= {maxy}
    """
    arrow_table = conn.execute(query).fetch_arrow_table()
    df = arrow_table.to_pandas()
    gdf = gpd.GeoDataFrame(
        df,
        geometry=df['geometry'].apply(wkt.loads),
        crs="EPSG:4326"
    )
    return gdf

## Load London area

In [4]:
# London bbox based on example on https://wiki.openstreetmap.org/wiki/Bounding_box
# We could derive this based on the GERS id, but not for now
london_bbox = (-0.489,51.28,0.236,51.686)

In [5]:
overturemaps_base = "/Volumes/PRO-G40/OvertureMaps/data/release/2025-08-20.0"

In [6]:
conn = duckdb_connection()

In [12]:
london_segments_gdf = load_area(conn, overturemaps_base, "transportation", "segment", london_bbox)

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [13]:
london_segments_gdf.head()

id  \
0  48a00d70-128e-43bf-a25c-ca462c11a0fd   
1  71fe3028-38f6-48a2-97cf-e06b59b2d8d1   
2  573b990e-c2c8-43d5-8e60-a94fe9460c10   
3  d3fa2c07-7852-4acf-90af-720e6ed6d946   
4  018dabad-91ea-4a65-828d-2bb4f68d91f8   

                                                bbox  version  \
0  {'xmin': -0.47854700684547424, 'xmax': -0.4778...        1   
1  {'xmin': -0.46354350447654724, 'xmax': -0.4561...        1   
2  {'xmin': -0.4549151062965393, 'xmax': -0.45467...        1   
3  {'xmin': -0.45137840509414673, 'xmax': -0.4513...        1   
4  {'xmin': -0.4553714096546173, 'xmax': -0.45446...        1   

                                             sources subtype    class names  \
0  [{'property': '', 'dataset': 'OpenStreetMap', ...    road    track  None   
1  [{'property': '', 'dataset': 'OpenStreetMap', ...    road    track  None   
2  [{'property': '', 'dataset': 'OpenStreetMap', ...    road  service  None   
3  [{'property': '', 'dataset': 'OpenStreetMap', ...    road  footway  None   
4  [{'property': '', 'dataset': 'OpenStreetMap', ...    road  service  None   

                                          connectors routes  \
0  [{'connector_id': 'df429e84-ef08-4021-b7e6-130...   None   
1  [{'connector_id': 'd8daf746-04a5-40cb-a2d4-4d4...   None   
2  [{'connector_id': 'c31f670d-bba6-403d-8d2f-60d...   None   
3  [{'connector_id': 'c8bca67f-b97b-4d36-a9ae-74f...   None   
4  [{'connector_id': '156f2ae5-8620-4837-833a-f1a...   None   

                                  subclass_rules  ... prohibited_transitions  \
0                                           None  ...                   None   
1                                           None  ...                   None   
2  [{'value': 'parking_aisle', 'between': None}]  ...                   None   
3                                           None  ...                   None   
4                                           None  ...                   None   

                              road_surface road_flags speed_limits  \
0                                     None       None         None   
1  [{'value': 'unpaved', 'between': None}]       None         None   
2                                     None       None         None   
3                                     None       None         None   
4                                     None       None         None   

  width_rules       subclass rail_flags           theme     type  \
0        None           None       None  transportation  segment   
1        None           None       None  transportation  segment   
2        None  parking_aisle       None  transportation  segment   
3        None           None       None  transportation  segment   
4        None           None       None  transportation  segment   

                                            geometry  
0  LINESTRING (-0.47855 51.2814, -0.47819 51.2813...  
1  LINESTRING (-0.46354 51.28084, -0.46261 51.281...  
2  LINESTRING (-0.45492 51.28084, -0.45468 51.280...  
3   LINESTRING (-0.45138 51.28092, -0.4513 51.28077)  
4   LINESTRING (-0.45446 51.28175, -0.45537 51.2815)  

[5 rows x 23 columns]

## Find subway connectors

Find the connectors that are attached to segments that are labelled as subways, implying these connectors are in the subway (tube).

In [31]:
def find_subway_segment_with_connectors(gdf):
    # restrict to only those segments that belong to a subway
    subway_segment_gdf = gdf[gdf["class"] == 'subway']
    
    # each segment has a list of connectors (stops along it)
    # create a dataframe which contains one row for each connector, along with all segment information
    exploded_gdf = subway_segment_gdf.explode("connectors")
    
    # create a new dataframe which contains a new `connector_id` column, but is indexed by the original `exploded_gdf` dataframe
    connectors_df = pd.DataFrame(exploded_gdf["connectors"].tolist(), index=exploded_gdf.index)

    # join it back to exploded df so we end up with a new `connector_id` on each repeated segment
    joined_gdf = exploded_gdf.join(connectors_df)connector_subsetted_gdf = connector_gdf.merge(subway_segment_gdf.loc[:,"connector_id"],
    left_on="id",
    right_on="connector_id",
    how="inner"
)
connector_subsetted_gdf.head()
    return joined_gdf

In [29]:
def find_subway_segment_with_connectors2(gdf):
    # restrict to only those segments that belong to a subway
    subway_segment_gdf = gdf[gdf["class"] == 'subway']
    
    # each segment has a list of connectors (stops along it)
    # create a dataframe which contains one row for each connector, along with all segment information
    exploded_gdf = subway_segment_gdf.explode("connectors")
    return exploded_gdf

In [21]:
foop_gdf = london_segments_gdf[london_segments_gdf["class"] == 'subway']
foop_gdf.head()

id  \
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37800  433ae8d9-b886-49ea-932f-e6dc95a7f2dc   
37847  7fef0a5e-3c50-4322-937d-83aa83826d10   
38136  d01ec415-79d3-4f22-9619-f8665e914600   
38264  4b17b6d7-d386-4eae-8610-184ec9e782e1   

                                                    bbox  version  \
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37800  {'xmin': -0.4517386555671692, 'xmax': -0.45136...        2   
37847  {'xmin': -0.4721474051475525, 'xmax': -0.42620...        1   
38136  {'xmin': -0.4612739086151123, 'xmax': -0.45920...        1   
38264  {'xmin': -0.459208607673645, 'xmax': -0.450624...        1   

                                                 sources subtype   class  \
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37800  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37847  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
38136  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
38264  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   

                                                   names  \
37799                                               None   
37800                                               None   
37847  {'primary': 'Piccadilly Line (Heathrow T4 Loop...   
38136  {'primary': 'Piccadilly Line (Heathrow T4 Loop...   
38264  {'primary': 'Piccadilly Line (Heathrow Branch)...   

                                              connectors routes  \
37799  [{'connector_id': 'cd3e6f86-9391-46c4-a52e-328...   None   
37800  [{'connector_id': 'a3989a4d-0b9c-4041-a941-82b...   None   
37847  [{'connector_id': '4f118903-29dd-411b-a637-917...   None   
38136  [{'connector_id': '2b21b8c0-7f24-4586-8a0c-944...   None   
38264  [{'connector_id': 'fc6e4164-ea8e-43f5-896d-355...   None   

      subclass_rules  ... prohibited_transitions road_surface road_flags  \
37799           None  ...                   None         None       None   
37800           None  ...                   None         None       None   
37847           None  ...                   None         None       None   
38136           None  ...                   None         None       None   
38264           None  ...                   None         None       None   

      speed_limits width_rules subclass  \
37799         None        None     None   
37800         None        None     None   
37847         None        None     None   
38136         None        None     None   
38264         None        None     None   

                                         rail_flags           theme     type  \
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37800  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37847  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
38136  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
38264  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   

                                                geometry  
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...  
37800  LINESTRING (-0.45136 51.47077, -0.45156 51.470...  
37847  LINESTRING (-0.4262 51.46616, -0.42963 51.4657...  
38136  LINESTRING (-0.46127 51.47318, -0.46072 51.473...  
38264  LINESTRING (-0.45062 51.47037, -0.45136 51.470...  

[5 rows x 23 columns]

In [22]:
foop_exploded_gdf = foop_gdf.explode("connectors")
foop_exploded_gdf.head()


id  \
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37800  433ae8d9-b886-49ea-932f-e6dc95a7f2dc   
37800  433ae8d9-b886-49ea-932f-e6dc95a7f2dc   

                                                    bbox  version  \
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37800  {'xmin': -0.4517386555671692, 'xmax': -0.45136...        2   
37800  {'xmin': -0.4517386555671692, 'xmax': -0.45136...        2   

                                                 sources subtype   class  \
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37800  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37800  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   

      names                                         connectors routes  \
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   
37799  None  {'connector_id': 'b1e52e14-c13b-4894-954d-5cef...   None   
37800  None  {'connector_id': 'a3989a4d-0b9c-4041-a941-82b5...   None   
37800  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   

      subclass_rules  ... prohibited_transitions road_surface road_flags  \
37799           None  ...                   None         None       None   
37799           None  ...                   None         None       None   
37799           None  ...                   None         None       None   
37800           None  ...                   None         None       None   
37800           None  ...                   None         None       None   

      speed_limits width_rules subclass  \
37799         None        None     None   
37799         None        None     None   
37799         None        None     None   
37800         None        None     None   
37800         None        None     None   

                                         rail_flags           theme     type  \
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37800  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37800  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   

                                                geometry  
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...  
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...  
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...  
37800  LINESTRING (-0.45136 51.47077, -0.45156 51.470...  
37800  LINESTRING (-0.45136 51.47077, -0.45156 51.470...  

[5 rows x 23 columns]

In [23]:
foop_connectors_df = pd.DataFrame(foop_exploded_gdf["connectors"].tolist(), index=foop_exploded_gdf.index)
foop_connectors_df.head()

connector_id        at
37799  cd3e6f86-9391-46c4-a52e-3285aa6726bd  0.000000
37799  31eca4ee-4292-4102-b0a0-de471813d30f  0.503344
37799  b1e52e14-c13b-4894-954d-5cef6cfbb60a  1.000000
37800  a3989a4d-0b9c-4041-a941-82b5429da7a0  0.000000
37800  31eca4ee-4292-4102-b0a0-de471813d30f  0.517846

In [24]:
foop_joined_gdf = foop_exploded_gdf.join(foop_connectors_df)
foop_joined_gdf.head()

id  \
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   

                                                    bbox  version  \
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   

                                                 sources subtype   class  \
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   

      names                                         connectors routes  \
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   
37799  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   

      subclass_rules  ... road_flags speed_limits width_rules subclass  \
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   

                                         rail_flags           theme     type  \
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   

                                                geometry  \
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   

                               connector_id        at  
37799  cd3e6f86-9391-46c4-a52e-3285aa6726bd  0.000000  
37799  31eca4ee-4292-4102-b0a0-de471813d30f  0.503344  
37799  b1e52e14-c13b-4894-954d-5cef6cfbb60a  1.000000  
37799  cd3e6f86-9391-46c4-a52e-3285aa6726bd  0.000000  
37799  31eca4ee-4292-4102-b0a0-de471813d30f  0.503344  

[5 rows x 25 columns]

In [19]:
london_subway_segment_gdf = find_subway_segment_with_connectors(london_segments_gdf)
london_subway_segment_gdf.head()

id  \
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   

                                                    bbox  version  \
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   

                                                 sources subtype   class  \
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   

      names                                         connectors routes  \
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   
37799  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   

      subclass_rules  ... road_flags speed_limits width_rules subclass  \
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   
37799           None  ...       None         None        None     None   

                                         rail_flags           theme     type  \
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   

                                                geometry  \
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...   

                               connector_id        at  
37799  cd3e6f86-9391-46c4-a52e-3285aa6726bd  0.000000  
37799  31eca4ee-4292-4102-b0a0-de471813d30f  0.503344  
37799  b1e52e14-c13b-4894-954d-5cef6cfbb60a  1.000000  
37799  cd3e6f86-9391-46c4-a52e-3285aa6726bd  0.000000  
37799  31eca4ee-4292-4102-b0a0-de471813d30f  0.503344  

[5 rows x 25 columns]

In [28]:
type(london_subway_segment_gdf)

geopandas.geodataframe.GeoDataFrame

In [26]:
london_subway_segment2_gdf = find_subway_segment_with_connectors2(london_segments_gdf)
london_subway_segment2_gdf.head()

id  \
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37799  891eae2c-32aa-47d6-a51c-5b5f538e89a9   
37800  433ae8d9-b886-49ea-932f-e6dc95a7f2dc   
37800  433ae8d9-b886-49ea-932f-e6dc95a7f2dc   

                                                    bbox  version  \
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37799  {'xmin': -0.45187580585479736, 'xmax': -0.4512...        2   
37800  {'xmin': -0.4517386555671692, 'xmax': -0.45136...        2   
37800  {'xmin': -0.4517386555671692, 'xmax': -0.45136...        2   

                                                 sources subtype   class  \
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37799  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37800  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   
37800  [{'property': '', 'dataset': 'OpenStreetMap', ...    rail  subway   

      names                                         connectors routes  \
37799  None  {'connector_id': 'cd3e6f86-9391-46c4-a52e-3285...   None   
37799  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   
37799  None  {'connector_id': 'b1e52e14-c13b-4894-954d-5cef...   None   
37800  None  {'connector_id': 'a3989a4d-0b9c-4041-a941-82b5...   None   
37800  None  {'connector_id': '31eca4ee-4292-4102-b0a0-de47...   None   

      subclass_rules  ... prohibited_transitions road_surface road_flags  \
37799           None  ...                   None         None       None   
37799           None  ...                   None         None       None   
37799           None  ...                   None         None       None   
37800           None  ...                   None         None       None   
37800           None  ...                   None         None       None   

      speed_limits width_rules subclass  \
37799         None        None     None   
37799         None        None     None   
37799         None        None     None   
37800         None        None     None   
37800         None        None     None   

                                         rail_flags           theme     type  \
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37799  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37800  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   
37800  [{'values': ['is_tunnel'], 'between': None}]  transportation  segment   

                                                geometry  
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...  
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...  
37799  LINESTRING (-0.45188 51.47099, -0.45156 51.470...  
37800  LINESTRING (-0.45136 51.47077, -0.45156 51.470...  
37800  LINESTRING (-0.45136 51.47077, -0.45156 51.470...  

[5 rows x 23 columns]

In [30]:
london_connectors_gdf = load_area(conn, overturemaps_base, "transportation", "connector", london_bbox)
london_connectors_gdf.head()

id  \
0  3b15b02c-09e0-49cb-b7f5-85ebab7a12dd   
1  0dfeb3db-0a74-4569-8c6e-0b0935998cad   
2  df429e84-ef08-4021-b7e6-13044338b0b2   
3  b0b520e4-1e88-46ed-8021-1eb2748520e9   
4  412eb849-5391-44c3-abe6-0498e7e6c672   

                                                bbox  version  \
0  {'xmin': -0.4876331090927124, 'xmax': -0.48763...        1   
1  {'xmin': -0.484427809715271, 'xmax': -0.484427...        1   
2  {'xmin': -0.47854700684547424, 'xmax': -0.4785...        1   
3  {'xmin': -0.47818654775619507, 'xmax': -0.4781...        1   
4  {'xmin': -0.4778040051460266, 'xmax': -0.47780...        1   

                                             sources           theme  \
0  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
1  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
2  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
3  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
4  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   

        type                   geometry  
0  connector  POINT (-0.48763 51.28405)  
1  connector  POINT (-0.48443 51.28203)  
2  connector   POINT (-0.47855 51.2814)  
3  connector  POINT (-0.47819 51.28135)  
4  connector    POINT (-0.4778 51.2813)

In [33]:
london_connectors_subsetted_gdf = london_connectors_gdf.merge(london_subway_segment_gdf.loc[:,"connector_id"],
    left_on="id",
    right_on="connector_id",
    how="inner"
)
london_connectors_subsetted_gdf.head()

id  \
0  d06fd930-25df-4535-a32f-6254bf05997f   
1  d06fd930-25df-4535-a32f-6254bf05997f   
2  d06fd930-25df-4535-a32f-6254bf05997f   
3  d06fd930-25df-4535-a32f-6254bf05997f   
4  31eca4ee-4292-4102-b0a0-de471813d30f   

                                                bbox  version  \
0  {'xmin': -0.44472235441207886, 'xmax': -0.4447...        1   
1  {'xmin': -0.44472235441207886, 'xmax': -0.4447...        1   
2  {'xmin': -0.44472235441207886, 'xmax': -0.4447...        1   
3  {'xmin': -0.44472235441207886, 'xmax': -0.4447...        1   
4  {'xmin': -0.45155805349349976, 'xmax': -0.4515...        1   

                                             sources           theme  \
0  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
1  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
2  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
3  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
4  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   

        type                   geometry                          connector_id  
0  connector  POINT (-0.44472 51.45927)  d06fd930-25df-4535-a32f-6254bf05997f  
1  connector  POINT (-0.44472 51.45927)  d06fd930-25df-4535-a32f-6254bf05997f  
2  connector  POINT (-0.44472 51.45927)  d06fd930-25df-4535-a32f-6254bf05997f  
3  connector  POINT (-0.44472 51.45927)  d06fd930-25df-4535-a32f-6254bf05997f  
4  connector  POINT (-0.45156 51.47093)  31eca4ee-4292-4102-b0a0-de471813d30f

In [34]:
london_connectors_subsetted_unique_gdf = london_connectors_subsetted_gdf.drop_duplicates(subset='id')
london_connectors_subsetted_unique_gdf.head()

id  \
0   d06fd930-25df-4535-a32f-6254bf05997f   
4   31eca4ee-4292-4102-b0a0-de471813d30f   
10  a3989a4d-0b9c-4041-a941-82b5429da7a0   
17  b1e52e14-c13b-4894-954d-5cef6cfbb60a   
27  fc6e4164-ea8e-43f5-896d-35503b1b9712   

                                                 bbox  version  \
0   {'xmin': -0.44472235441207886, 'xmax': -0.4447...        1   
4   {'xmin': -0.45155805349349976, 'xmax': -0.4515...        1   
10  {'xmin': -0.45136401057243347, 'xmax': -0.4513...        1   
17  {'xmin': -0.45124441385269165, 'xmax': -0.4512...        1   
27  {'xmin': -0.4506247043609619, 'xmax': -0.45062...        1   

                                              sources           theme  \
0   [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
4   [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
10  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
17  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   
27  [{'property': '', 'dataset': 'OpenStreetMap', ...  transportation   

         type                   geometry                          connector_id  
0   connector  POINT (-0.44472 51.45927)  d06fd930-25df-4535-a32f-6254bf05997f  
4   connector  POINT (-0.45156 51.47093)  31eca4ee-4292-4102-b0a0-de471813d30f  
10  connector  POINT (-0.45136 51.47077)  a3989a4d-0b9c-4041-a941-82b5429da7a0  
17  connector  POINT (-0.45124 51.47087)  b1e52e14-c13b-4894-954d-5cef6cfbb60a  
27  connector  POINT (-0.45062 51.47037)  fc6e4164-ea8e-43f5-896d-35503b1b9712

In [35]:
london_connectors_subsetted_unique_gdf.explore()

In [38]:
london_connectors_subsetted_unique_gdf.explore(tiles="CartoDB positron")